# 2-D (RR) Arm

In [6]:
import numpy as np

# --- Robot Parameters ---
# Link lengths (assuming values from the first image)
length_link_1 = 1
length_link_2 = 1

# Target end-effector position
x_f = np.array([1.5, 0.5])

# Initial joint angles (in radians)
theta_current = np.array([np.pi/4, np.pi/4])

# --- Algorithm Parameters ---
max_iterations = 100  # Maximum number of iterations to prevent infinite loops
tolerance = 1e-3      # Stop when the error norm is below this value
beta = 0.05   # Beta factor

# --- Data Storage for Animation ---
theta_sequence = [theta_current.copy()] # Store initial state
position_sequence = [] # Store end-effector positions

# --- Sanity check to ensure if position is reachable or not ---
if np.linalg.norm(x_f) > (length_link_1 + length_link_2):
  print("Position not reachable - run demo at your own risk!")

In [7]:
# --- Functions ---
def forward_kinematics(theta, l1, l2):
  """
  Calculates the end-effector position for a 2R arm.
  Args:
    theta: Numpy array of joint angles [theta1, theta2] in radians.
    l1: Length of the first link.
    l2: Length of the second link.
  Returns:
    Numpy array of end-effector position [x, y].
  """

  theta1 = theta[0]
  theta2 = theta[1]
  x = l1 * np.cos(theta1) + l2 * np.cos(theta1 + theta2)
  y = l1 * np.sin(theta1) + l2 * np.sin(theta1 + theta2)

  x_elbow = l1 * np.cos(theta1)
  y_elbow = l1 * np.sin(theta1)

  x_ee = x_elbow + l2 * np.cos(theta1 + theta2)
  y_ee = y_elbow + l2 * np.sin(theta1 + theta2)
  return np.array([x_elbow, y_elbow]), np.array([x_ee, y_ee])

def calculate_jacobian(theta, l1, l2):
  """
  Calculates the Jacobian matrix for a 2R arm.
  Args:
    theta: Numpy array of joint angles [theta1, theta2] in radians.
    l1: Length of the first link.
    l2: Length of the second link.
  Returns:
    2x2 Numpy array representing the Jacobian matrix.
  """
  theta1 = theta[0]
  theta2 = theta[1]
  s1 = np.sin(theta1)
  c1 = np.cos(theta1)
  s12 = np.sin(theta1 + theta2)
  c12 = np.cos(theta1 + theta2)

  J = np.array([
      [-l1 * s1 - l2 * s12, -l2 * s12],
      [ l1 * c1 + l2 * c12,  l2 * c12]
  ])
  return J

In [8]:
# --- Iterative Inverse Kinematics Loop ---

print(f"Target Position: {x_f}")
print(f"Initial Angles (rad): {theta_current}")
print("-" * 30)

for i in range(max_iterations):
  # 1. Calculate current end-effector position
  elbow_pos, x_current = forward_kinematics(theta_current, length_link_1, length_link_2)
  position_sequence.append(x_current.copy())

  # 2. Calculate the error vector
  delta_x = x_f - x_current
  error_norm = np.linalg.norm(delta_x)

  print(f"Iteration {i+1}:")
  print(f"  Current Angles (rad): {theta_current}")
  print(f"  Current Position:    {x_current}")
  print(f"  Target Position:     {x_f}")
  print(f"  Error Vector (dx):   {delta_x}")
  print(f"  Error Norm:          {error_norm:.6f}")

  # 3. Check for convergence
  if error_norm < tolerance:
    print("Convergence achieved!\n")
    break

  # 4. Calculate the Jacobian at the current configuration
  J = calculate_jacobian(theta_current, length_link_1, length_link_2)

  # 5. Calculate the Jacobian inverse
  try:
    # Check determinant before inverting
    det_J = np.linalg.det(J)
    # if np.abs(det_J) < 1e-3: # Check if close to singular -> can adjust threshold
    #     print("Warning: Jacobian is close to singular. Stopping.\n")
    #     break
    J_inv = np.linalg.inv(J) #inverse calculation
  except np.linalg.LinAlgError:
    print("Error: Jacobian is singular, cannot invert. Stopping.\n")
    break

  # 6. Calculate the change in joint angles
  delta_theta = J_inv @ delta_x

  # 7. Update the joint angles
  theta_current = theta_current + beta * delta_theta
  theta_sequence.append(theta_current.copy())

  print(f"  Jacobian Det:        {det_J:.6f}")
  print(f"  Delta Theta (rad):   {delta_theta}")
  print("-" * 30)

else:
    print(f"\nMaximum iterations ({max_iterations}) reached without convergence.")
    print(f"Final error norm: {error_norm:.6f}")

# --- Final Results ---
print("\n" + "=" * 30)
print("Final Results:")
print(f"  Target Position:     {x_f}")
print(f"  Final Angles (rad):  {theta_current}")
_, final_pos = forward_kinematics(theta_current, length_link_1, length_link_2)
position_sequence.append(final_pos)
print(f"  Final Position:      {final_pos}")
print(f"  Final Error Norm:    {np.linalg.norm(x_f - final_pos):.6f}")
print("=" * 30)

Target Position: [1.5 0.5]
Initial Angles (rad): [0.78539816 0.78539816]
------------------------------
Iteration 1:
  Current Angles (rad): [0.78539816 0.78539816]
  Current Position:    [0.70710678 1.70710678]
  Target Position:     [1.5 0.5]
  Error Vector (dx):   [ 0.79289322 -1.20710678]
  Error Norm:          1.444225
  Jacobian Det:        0.707107
  Delta Theta (rad):   [-1.70710678  2.12132034]
------------------------------
Iteration 2:
  Current Angles (rad): [0.70004282 0.89146418]
  Current Position:    [0.7441054  1.64403598]
  Target Position:     [1.5 0.5]
  Error Vector (dx):   [ 0.7558946  -1.14403598]
  Error Norm:          1.371202
  Jacobian Det:        0.777992
  Delta Theta (rad):   [-1.49030309  1.69458072]
------------------------------
Iteration 3:
  Current Angles (rad): [0.62552767 0.97619322]
  Current Position:    [0.77973464 1.58504699]
  Target Position:     [1.5 0.5]
  Error Vector (dx):   [ 0.72026536 -1.08504699]
  Error Norm:          1.302348
  Jaco

In [9]:
import matplotlib.pyplot as plt
from matplotlib import animation, rcParams
from IPython.display import HTML, display

fig, ax = plt.subplots(figsize=(7, 7)) 
fig.patch.set_facecolor('black') 
ax.set_facecolor('black') 
rcParams['axes.edgecolor'] = 'white' 
rcParams['xtick.color'] = 'white'  
rcParams['ytick.color'] = 'white'  
rcParams['axes.labelcolor'] = 'white'
rcParams['axes.titlecolor'] = 'white' 

all_x = [0] + [forward_kinematics(th, length_link_1, length_link_2)[0][0] for th in theta_sequence] + \
        [forward_kinematics(th, length_link_1, length_link_2)[1][0] for th in theta_sequence] + [x_f[0]]
all_y = [0] + [forward_kinematics(th, length_link_1, length_link_2)[0][1] for th in theta_sequence] + \
        [forward_kinematics(th, length_link_1, length_link_2)[1][1] for th in theta_sequence] + [x_f[1]]

buffer = 0.5 
x_min, x_max = min(all_x) - buffer, max(all_x) + buffer
y_min, y_max = min(all_y) - buffer, max(all_y) + buffer
max_range = max(x_max - x_min, y_max - y_min) 

# Initialize plot elements that will be updated
line, = ax.plot([], [], 'o-', lw=3, color='cyan', markersize=8, markerfacecolor='lightblue') 
base_dot, = ax.plot([], [], 'wo', markersize=10) # base joint
elbow_dot, = ax.plot([], [], 'o', color='magenta', markersize=8) # elbow joint
ee_dot, = ax.plot([], [], 'o', color='lime', markersize=8) # ee
target_dot, = ax.plot([], [], 'yx', markersize=12, markeredgewidth=3) # target
title = ax.set_title('')

def init():
    ax.set_xlim(x_min, x_min + max_range) 
    ax.set_ylim(y_min, y_min + max_range)
    ax.set_xlabel("X position")
    ax.set_ylabel("Y position")
    ax.set_aspect('equal', adjustable='box')
    ax.grid(True, linestyle='--', alpha=0.6)
    target_dot.set_data([x_f[0]], [x_f[1]]) 
    base_dot.set_data([0], [0])
    line.set_data([], [])
    elbow_dot.set_data([],[])
    ee_dot.set_data([],[])
    title.set_text('')
    for spine in ax.spines.values():
        spine.set_edgecolor('white')
    return line, base_dot, elbow_dot, ee_dot, target_dot, title,

def update_frame(frame):
    theta = theta_sequence[frame]
    elbow_pos, ee_pos = forward_kinematics(theta, length_link_1, length_link_2)

    x_data = [0, elbow_pos[0], ee_pos[0]]
    y_data = [0, elbow_pos[1], ee_pos[1]]
    line.set_data(x_data, y_data)

    elbow_dot.set_data([elbow_pos[0]], [elbow_pos[1]])
    ee_dot.set_data([ee_pos[0]], [ee_pos[1]])

    title.set_text(f'Iteration: {frame + 1}/{len(theta_sequence)}')

    return line, elbow_dot, ee_dot, title

if len(theta_sequence) > 1:
    print("Creating animation...")
    num_frames = len(theta_sequence)
    anim = animation.FuncAnimation(fig, update_frame, frames=num_frames,
                                   init_func=init, interval=100, blit=True)
    try:
        display(HTML(anim.to_jshtml()))
        plt.close(fig)
        print("Animation displayed.")
    except Exception as e:
        print(f"Could not display animation inline: {e}")
        print("Showing static plot of the final frame instead.")
        init()
        update_frame(len(theta_sequence) - 1)
        plt.show()

elif len(theta_sequence) == 1:
     print("Only initial state available. Plotting initial state.")
     init()
     update_frame(0)
     plt.show()
else:
     print("No data generated for animation.")
# rcParams.update(rcParams.defaults)

Creating animation...


Animation displayed.
